# Load CMIP6 Data with Intake ESM

[Intake ESM](https://intake-esm.readthedocs.io/en/latest/) is an experimental new package that aims to provide a higher-level interface to searching and loading Earth System Model data archives, such as CMIP6. The packages is under very active development, and features may be unstable. Please report any issues or suggestions [on github](https://github.com/NCAR/intake-esm/issues).

In [1]:
import xarray as xr
xr.set_options(display_style='html')
import intake
%matplotlib inline

Intake ESM works by parsing an [ESM Collection Spec](https://github.com/NCAR/esm-collection-spec/) and converting it to an [intake catalog](https://intake.readthedocs.io/en/latest). The collection spec is stored in a .json file. Here we open it using intake.

In [2]:
cat_url = "https://storage.googleapis.com/cmip6/pangeo-cmip6.json"
col = intake.open_esm_datastore(cat_url)
col

pangeo-cmip6-ESM Collection with 235624 entries:
	> 15 activity_id(s)

	> 32 institution_id(s)

	> 69 source_id(s)

	> 101 experiment_id(s)

	> 135 member_id(s)

	> 29 table_id(s)

	> 313 variable_id(s)

	> 10 grid_label(s)

	> 235624 zstore(s)

	> 60 dcpp_init_year(s)

We can now use intake methods to search the collection, and, if desired, export a pandas dataframe.

In [3]:
cat = col.search(experiment_id=['historical', 'ssp585'], table_id='Oyr', variable_id='o2',
                 grid_label='gn')
cat.df

activity_id institution_id      source_id experiment_id  member_id  \
0           CMIP          CCCma  CanESM5-CanOE    historical   r1i1p2f1   
1           CMIP          CCCma  CanESM5-CanOE    historical   r2i1p2f1   
2           CMIP          CCCma  CanESM5-CanOE    historical   r3i1p2f1   
3           CMIP          CCCma        CanESM5    historical  r10i1p1f1   
4           CMIP          CCCma        CanESM5    historical  r10i1p2f1   
..           ...            ...            ...           ...        ...   
132  ScenarioMIP           IPSL   IPSL-CM6A-LR        ssp585   r4i1p1f1   
133  ScenarioMIP           IPSL   IPSL-CM6A-LR        ssp585   r6i1p1f1   
134  ScenarioMIP          MIROC     MIROC-ES2L        ssp585   r1i1p1f2   
135  ScenarioMIP          MPI-M  MPI-ESM1-2-LR        ssp585  r10i1p1f1   
136  ScenarioMIP          MPI-M  MPI-ESM1-2-LR        ssp585   r1i1p1f1   

    table_id variable_id grid_label  \
0        Oyr          o2         gn   
1        Oyr          o2         gn   
2        Oyr          o2         gn   
3        Oyr          o2         gn   
4        Oyr          o2         gn   
..       ...         ...        ...   
132      Oyr          o2         gn   
133      Oyr          o2         gn   
134      Oyr          o2         gn   
135      Oyr          o2         gn   
136      Oyr          o2         gn   

                                                zstore  dcpp_init_year  
0    gs://cmip6/CMIP/CCCma/CanESM5-CanOE/historical...             NaN  
1    gs://cmip6/CMIP/CCCma/CanESM5-CanOE/historical...             NaN  
2    gs://cmip6/CMIP/CCCma/CanESM5-CanOE/historical...             NaN  
3    gs://cmip6/CMIP/CCCma/CanESM5/historical/r10i1...             NaN  
4    gs://cmip6/CMIP/CCCma/CanESM5/historical/r10i1...             NaN  
..                                                 ...             ...  
132  gs://cmip6/ScenarioMIP/IPSL/IPSL-CM6A-LR/ssp58...             NaN  
133  gs://cmip6/ScenarioMIP/IPSL/IPSL-CM6A-LR/ssp58...             NaN  
134  gs://cmip6/ScenarioMIP/MIROC/MIROC-ES2L/ssp585...             NaN  
135  gs://cmip6/ScenarioMIP/MPI-M/MPI-ESM1-2-LR/ssp...             NaN  
136  gs://cmip6/ScenarioMIP/MPI-M/MPI-ESM1-2-LR/ssp...             NaN  

[137 rows x 10 columns]

Intake knows how to automatically open the datasets using xarray. Furthermore, intake esm contains special logic to concatenate and merge the individual results of our query into larger, more high-level aggregated xarray datasets.

In [4]:
dset_dict = cat.to_dataset_dict(zarr_kwargs={'consolidated': True})
list(dset_dict.keys())


--> The keys in the returned dictionary of datasets are constructed as follows:
	'activity_id.institution_id.source_id.experiment_id.table_id.grid_label'
                
--> There is/are 17 group(s)
[########################################] | 100% Completed |  1min 27.1s


['CMIP.CCCma.CanESM5.historical.Oyr.gn',
 'CMIP.CCCma.CanESM5-CanOE.historical.Oyr.gn',
 'CMIP.CSIRO.ACCESS-ESM1-5.historical.Oyr.gn',
 'CMIP.HAMMOZ-Consortium.MPI-ESM-1-2-HAM.historical.Oyr.gn',
 'CMIP.IPSL.IPSL-CM6A-LR.historical.Oyr.gn',
 'CMIP.MIROC.MIROC-ES2L.historical.Oyr.gn',
 'CMIP.MPI-M.MPI-ESM1-2-HR.historical.Oyr.gn',
 'CMIP.MPI-M.MPI-ESM1-2-LR.historical.Oyr.gn',
 'CMIP.NCC.NorESM2-LM.historical.Oyr.gn',
 'ScenarioMIP.CCCma.CanESM5.ssp585.Oyr.gn',
 'ScenarioMIP.CCCma.CanESM5-CanOE.ssp585.Oyr.gn',
 'ScenarioMIP.CSIRO.ACCESS-ESM1-5.ssp585.Oyr.gn',
 'ScenarioMIP.DKRZ.MPI-ESM1-2-HR.ssp585.Oyr.gn',
 'ScenarioMIP.DWD.MPI-ESM1-2-HR.ssp585.Oyr.gn',
 'ScenarioMIP.IPSL.IPSL-CM6A-LR.ssp585.Oyr.gn',
 'ScenarioMIP.MIROC.MIROC-ES2L.ssp585.Oyr.gn',
 'ScenarioMIP.MPI-M.MPI-ESM1-2-LR.ssp585.Oyr.gn']

In [5]:
ds = dset_dict['CMIP.CCCma.CanESM5.historical.Oyr.gn']
ds

<xarray.Dataset>
Dimensions:             (bnds: 2, i: 360, j: 291, lev: 45, member_id: 35, time: 165, vertices: 4)
Coordinates:
    longitude           (j, i) float64 dask.array<chunksize=(291, 360), meta=np.ndarray>
    lev_bnds            (lev, bnds) float64 dask.array<chunksize=(45, 2), meta=np.ndarray>
    latitude            (j, i) float64 dask.array<chunksize=(291, 360), meta=np.ndarray>
    time_bnds           (time, bnds) object dask.array<chunksize=(165, 2), meta=np.ndarray>
  * j                   (j) int32 0 1 2 3 4 5 6 ... 284 285 286 287 288 289 290
  * time                (time) object 1850-07-02 12:00:00 ... 2014-07-02 12:00:00
  * i                   (i) int32 0 1 2 3 4 5 6 ... 353 354 355 356 357 358 359
  * lev                 (lev) float64 3.047 9.454 16.36 ... 5.375e+03 5.625e+03
  * member_id           (member_id) <U9 'r10i1p1f1' 'r10i1p2f1' ... 'r9i1p2f1'
Dimensions without coordinates: bnds, vertices
Data variables:
    vertices_latitude   (j, i, vertices) float64 dask.array<chunksize=(291, 360, 4), meta=np.ndarray>
    vertices_longitude  (j, i, vertices) float64 dask.array<chunksize=(291, 360, 4), meta=np.ndarray>
    o2                  (member_id, time, lev, j, i) float32 dask.array<chunksize=(1, 12, 45, 291, 360), meta=np.ndarray>
Attributes:
    contact:                     ec.cccma.info-info.ccmac.ec@canada.ca
    parent_activity_id:          CMIP
    license:                     CMIP6 model data produced by The Government ...
    intake_esm_varname:          o2
    mip_era:                     CMIP6
    Conventions:                 CF-1.7 CMIP-6.2
    variable_id:                 o2
    version:                     v20190429
    source_type:                 AOGCM
    variant_label:               r9i1p2f1
    table_id:                    Oyr
    external_variables:          areacello volcello
    cmor_version:                3.4.0
    references:                  Geophysical Model Development Special issue ...
    institution_id:              CCCma
    forcing_index:               1
    source:                      CanESM5 (2019): \naerosol: interactive\natmo...
    realization_index:           9
    CCCma_parent_runid:          p2-pictrl
    tracking_id:                 hdl:21.14100/41426118-701c-482b-ae16-82932e4...
    initialization_index:        1
    branch_method:               Spin-up documentation
    status:                      2019-10-25;created;by nhn2@columbia.edu
    table_info:                  Creation Date:(20 February 2019) MD5:374fbe5...
    activity_id:                 CMIP
    YMDH_branch_time_in_parent:  5950:01:01:00
    creation_date:               2019-05-30T08:58:45Z
    product:                     model-output
    YMDH_branch_time_in_child:   1850:01:01:00
    frequency:                   yr
    data_specs_version:          01.00.29
    experiment:                  all-forcing simulation of the recent past
    CCCma_model_hash:            Unknown
    branch_time_in_parent:       1496500.0
    institution:                 Canadian Centre for Climate Modelling and An...
    parent_source_id:            CanESM5
    sub_experiment_id:           none
    nominal_resolution:          100 km
    parent_experiment_id:        piControl
    further_info_url:            https://furtherinfo.es-doc.org/CMIP6.CCCma.C...
    source_id:                   CanESM5
    history:                     2019-05-02T13:53:53Z ;rewrote data to be con...
    CCCma_runid:                 p2-his09
    grid_label:                  gn
    title:                       CanESM5 output prepared for CMIP6
    parent_time_units:           days since 1850-01-01 0:0:0.0
    grid:                        ORCA1 tripolar grid, 1 deg with refinement t...
    experiment_id:               historical
    branch_time_in_child:        0.0
    sub_experiment:              none
    realm:                       ocnBgchem
    parent_mip_era:              CMIP6